In [111]:
import json
import torch

from tqdm import tqdm
from functools import partial
from torch.utils.data import DataLoader
from torch.utils.data.dataset import Dataset
from transformers import AutoTokenizer, AutoConfig, AutoModelForSeq2SeqLM

In [27]:
def read_jsonl(file_path):
    with open(file_path, "r") as f:
        data = [json.loads(line) for line in f]
    return data

In [89]:
tokenizer_name = "google/mt5-small"
model_name_or_path = "google/mt5-small"
batch_size = 4

In [50]:
TEXT_COL = "maintext"
SUMMARY_COL = "title"
MAX_SOURCE_LEN = 1024
MAX_TARGET_LEN = 128

In [56]:
file_path = "data/data/train.jsonl"
train_data_list = read_jsonl(file_path)
train_data_list[0].keys()

dict_keys(['date_publish', 'title', 'source_domain', 'maintext', 'split', 'id'])

In [38]:
tokenizer = AutoTokenizer.from_pretrained(
    tokenizer_name,
    use_fast=True,
    trust_remote_code=False
)

In [45]:
model_config = AutoConfig.from_pretrained(model_name_or_path, trust_remote_code=False)
model = AutoModelForSeq2SeqLM.from_pretrained(
    model_name_or_path,
    config=model_config,
    trust_remote_code=False,
)

In [100]:
def preprocess_func(data, tokenizer):
    tokenized_data = tokenizer(data[TEXT_COL], max_length=MAX_SOURCE_LEN, padding="max_length", truncation=True)
    label = tokenizer(text_target=data[SUMMARY_COL], max_length=MAX_TARGET_LEN, padding="max_length", truncation=True)["input_ids"]
    label = [(l if l != tokenizer.pad_token_id else -100) for l in label]
    tokenized_data["labels"] = label
    return tokenized_data


def postprocess_func(batch_data):
    return ["\n".join(nltk.sent_tokenize(data.strip())) for data in batch_data]

In [109]:
class ChineseNewsDataset(Dataset):
    def __init__(self, data_list, transform=False):
        self.data_list = [transform(data) for data in tqdm(data_list)] if transform is not None else data_list
        self.data_list = [dict((k, torch.tensor(v)) for k, v in data.items()) for data in self.data_list]

    def __len__(self):
        return len(self.data_list)

    def __getitem__(self, index):
        return self.data_list[index]

In [112]:
preprocess_func = partial(preprocess_func, tokenizer=tokenizer)
train_dataset = ChineseNewsDataset(train_data_list, preprocess_func)

100%|██████████████████████████████████████████████████████████████████████████| 21710/21710 [00:21<00:00, 988.70it/s]


In [113]:
for data in train_dataset:
    print(data)
    break

{'input_ids': tensor([  259, 71934,  2144,  ..., 13440,   261,     1]), 'attention_mask': tensor([1, 1, 1,  ..., 1, 1, 1]), 'labels': tensor([   259,  74378,   9734,  22399,   4457,   1146,  91653,   9139, 171388,
         26473,  31225,    259,    292,   2230, 200229, 192250,   4066,  23281,
          2910,   4565,  86305,  95289, 241245, 178273,  63687,  18540, 137179,
          1193, 175062,  23823,   4457,  12307,  11072,      1,   -100,   -100,
          -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,
          -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,
          -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,
          -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,
          -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,
          -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,   -100,
          -100,   -100,   -100,   -100,   -100,   -100,   -100,   

In [114]:
train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)

In [121]:
for data in train_loader:
    print(data.keys())
    print(data["labels"].shape)
    break

dict_keys(['input_ids', 'attention_mask', 'labels'])
torch.Size([4, 128])


In [108]:
train_data_list

[{'date_publish': '2015-03-02 00:00:00',
  'title': '榜首進台大醫科卻休學 、27歲拿到法國天文博士 李悅寧跌破眾人眼鏡返台任教',
  'source_domain': 'udn.com',
  'maintext': '從小就很會念書的李悅寧， 在眾人殷殷期盼下，以榜首之姿進入臺大醫學院， 但始終忘不了對天文的熱情。大學四年級一場遠行後，她決心遠赴法國攻讀天文博士。 從小沒想過當老師的她，再度跌破眾人眼鏡返台任教， 只為幫助對天文有興趣的學生，少走點冤枉路。\n二○一九年九月開學日，臺灣師範大學地球科學系迎來創系三十五年來最年輕的助理教授、還不滿三十歲的李悅寧。 時間往前推半年多，科技部部長陳良基率團到歐洲，延攬海外優秀學術科研人才返國貢獻。在巴黎那場，科技部二○一九年「愛因斯坦培植計畫」得主之一的李悅寧，親自向陳良基報到，表達她打算返台，回臺師大任職，投入台灣天文研究行列的動向。\n這距離她到法國當交換學生，之後從臺大醫學系休學，轉換跑道留在法國念天文，整整七年。\n高中展露科學天分 卻務實選擇醫學系\n李悅寧就讀台中女中高三時期，身邊的同學大多忙著準備大學指考，她卻因緣際會接觸到地球科學，在老師鼓勵下參加首屆國際地球科學奧林匹亞競賽，沒想到一鳴驚人，抱回金牌及全球第二名。 在一片「聰明的人念醫學院，最厲害的人念臺大醫科」的氛圍中，二○○八年，李悅寧頂著當年大學指考第二、 三類組榜首的光環，很自然地在眾人期盼下進入臺大醫學院。 李悅寧坦言，儘管當時對地球科學及研究領域很有興趣，但「有點沒安全感」，想做點「安全、務實的事」；相形之下，醫學系所讀的知識不但務實，也都是之前沒學過的內容。她甚至想好了醫學院畢業之後，要往創傷重建的整形外科方向走。\n雖然進入醫學系就讀，李悅寧卻始終無法忘懷科學研究。除了從大二開始雙主修醫學系及機械工程系，每個暑假她幾乎都投身科學研究相關活動。 二○○九年及二○一○年暑假，在老師推薦與科技部前身國科會的經費支持下，李悅寧分別到法國巴黎出席國際天文年的開幕儀式、赴德國參加林島諾貝爾獎得主會議（Lindau Nobel Laureate Meeting），並自己找資訊，申請前往瑞士洛桑聯邦理工學院（EPFL），參加心理物理學相關活動。 大四升大五的暑假，李悅寧到中研院天文及天文物理研究所，